# Sentiment Analysis on Bitcoin via Tweets



MarketPulse Analytics, a leading company in the field of market research, has launched a project to estimate public consensus on Bitcoin by analyzing millions of tweets.
Your responsibility, as a Data Scientist, is to perform sentiment analysis on the collected data and understand how opinions regarding Bitcoin vary over time.
In addition, you will need to answer key questions about user engagement on social media and assess potential correlations with the price of Bitcoin.

1. The first step is to analyze the sentiment of tweets using a sentiment analysis model. For each extracted tweet, it will be classified as positive, negative, or neutral, based on keywords, tone, and language used. This classification will allow you to measure consensus toward Bitcoin on a daily basis.

2. Next, a time-series chart will be created to show the day-to-day sentiment variation:

  - Positive Tweets: The number of tweets with a positive sentiment on a daily basis.

  - Negative Tweets: The number of tweets with a negative sentiment on a daily basis.

  - Neutral Tweets: The trend of tweets that do not show a clear value judgment.

  The chart will illustrate the evolution of public sentiment toward Bitcoin, highlighting peaks or declines.

3. After sentiment analysis, it is interesting to evaluate the engagement generated by tweets. Specifically, you will answer these two questions:

  - Do negative tweets receive more likes compared to positive tweets? The averages of likes for negative and positive tweets will be calculated and compared, analyzing whether tweets with a negative tone attract more attention or interest.

  - Do negative tweets receive more interactions (replies) compared to positive tweets? A similar analysis will be conducted by comparing the average number of replies between positive and negative tweets, to see which type of sentiment sparks more intense discussions.

4. To add further depth to the analysis, you will explore the relationship between sentiment variation and Bitcoin’s price variation. For this purpose:

  - Retrieve Bitcoin price history (BTC/USD) from [here](https://github.com/Profession-AI/progetti-big-data/blob/main/Analisi%20del%20consenso%20sul%20Bitcoin/BTC-USD.csv).

  - Compare daily sentiment variations with Bitcoin price changes, aiming to identify significant correlations.

  This approach will allow you to answer the question:
  Does public sentiment toward Bitcoin influence the price of the cryptocurrency? Or, conversely, do price changes influence sentiment on social media?

## Added Value

Through this project, MarketPulse Analytics will obtain highly valuable insights:

- Understanding sentiment toward Bitcoin in real time, useful for investors and financial professionals.

- Identifying social trends related to the cryptocurrency, potentially able to anticipate market movements.

- Engagement behavior analysis: Understanding whether negative tweets attract more attention or generate more interactions compared to positive ones, useful for marketing strategies.

- Correlation between sentiment and Bitcoin price: Providing insights on how public sentiment can influence or be influenced by Bitcoin’s market value, offering new strategic perspectives for MarketPulse Analytics’ clients.

This analysis will provide a useful tool for data-driven business decisions, offering a competitive edge in the cryptocurrency market.

### Import

In [0]:
%pip install spark-nlp==6.2.0.*
%pip install emoji==2.15.0.*

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
#%restart_python

In [0]:
import pandas as pd
from functools import reduce

import emoji
from pyspark.sql import SparkSession
from pyspark.sql import functions as F
from pyspark.sql import types as T
from pyspark.sql.types import StringType

from pyspark.ml.feature import CountVectorizer, IDF, SQLTransformer
from pyspark.ml import Pipeline

import sparknlp

from sparknlp.base import DocumentAssembler, Finisher
from sparknlp.annotator import Tokenizer, Normalizer, StopWordsCleaner, LemmatizerModel
from sparknlp.annotator import LanguageDetectorDL




In [0]:
# Riutilizza la SparkSession di Databricks
spark = SparkSession.builder.getOrCreate()

print("Spark NLP version:", sparknlp.version())
print("Spark version:", spark.version)

Spark NLP version: 4.4.4
Spark version: 4.0.0


### Set default parameters



## Load data from web


Per poter caricare il dataframe e trasformarlo in una table puoi usare un Volume di DataBricks. Su Notebook Databricks esegui questo codice in celle separate:

%sql
CREATE CATALOG IF NOT EXISTS my_catalog;
CREATE SCHEMA  IF NOT EXISTS my_catalog.raw;
CREATE VOLUME  IF NOT EXISTS my_catalog.raw.datasets
%sh
mkdir -p /Volumes/my_catalog/raw/datasets
curl -L "https://proai-datasets.s3.eu-west-3.amazonaws.com/bitcoin_tweets.csv" \
  -o /Volumes/my_catalog/raw/datasets/bitcoin_tweets.csv
path = "/Volumes/my_catalog/raw/datasets/bitcoin_tweets.csv"
df = spark.read.csv(path, header=True, inferSchema=True)

In [0]:
# create the spark session
spark = SparkSession.builder.appName("TwitterSentiment").getOrCreate()

In [0]:
# dataset loading
dataset_path = "workspace.default.bitcoin_tweets"
df = spark.table(dataset_path)

# EDA

In [0]:
# count the number of rows
row_count = df.count()
row_count

230383

In [0]:
display(df)

id user fullname url timestamp replies likes retweets text 1.1329770553003008E18 KamdemAbdiel Abdiel kamdem null 2019-05-27T11:49:14.000Z 0.0 0.0 0.0 È appena uscito un nuovo video! LES CRYPTOMONNAIES QUI PULVÉRISENT BITCOIN EN 2019 https://t.co/yCsQMvRnyS 1.13297707340273664E18 bitcointe Bitcointe null 2019-05-27T11:49:18.000Z 0.0 0.0 0.0 Cardano: Digitize Currencies; EOS https://t.co/1kTKqKEBlS 6500% ROI; AT&T Bitcoin Bill Pay https://t.co/eQCwOXKHK0 | Cardano (ADA) 🌏📢😎🤑💵 | #FolloForFolloBack #follo4folloback #followforfollow #bitcointe #cryptocurrency 1.13297702389313958E18 3eyedbran Bran - 3 Eyed Raven null 2019-05-27T11:49:06.000Z 0.0 2.0 1.0 Another Test tweet that wasn't caught in the stream ! bitcoin 1.13297708908955635E18 DetroitCrypto J. Scardina null 2019-05-27T11:49:22.000Z 0.0 0.0 0.0 Current Crypto Prices! 
 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 1.13297709234019123E18 mmursaleen72 Muhammad Mursaleen null 2019-05-27T11:49:23.000Z 0.0 0.0 0.0 Spiv (Nosar Baz): BITCOIN Is An Asset & NOT A Currency.
 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 1.13297710030931955E18 0nurTOKA 🐻🔫💥🐂🚀🙏 null 2019-05-27T11:49:25.000Z 0.0 0.0 0.0 #btc inceldiği yerden kopsun bakalım 17:00 ye kadar bir hareket bekliyorum, yukarı yönlü olur umarın sanırım inşallah yani 😁 https://t.co/pIMyKfNtc8 1.13297710163889766E18 evilrobotted evilrobotted null 2019-05-27T11:49:25.000Z 0.0 0.0 0.0 @nwoodfine We have been building on the real #bitcoin SV.
 null null null null null null null null null 1.1329771088363232E18 jabur_guilherme Guilherme Jabur null 2019-05-27T11:49:27.000Z 0.0 0.0 0.0 @pedronauck como investidor, vc é um ótimo dev. Sorte q eu comprei os BTC, subiu a poha toda :o 1.13297713185035059E18 INTBICON 億り人彼氏 null 2019-05-27T11:49:32.000Z 0.0 0.0 0.0 ブラジルはまぁ置いといてもドイツは存在感出してくるのかな。ロシアもマイニングなどで元気になるかと思ったらそこまででしたね。
 null null null null null null null null null 1.13297713271456154E18 MLWright15 ML Wright null 2019-05-27T11:49:32.000Z 0.0 0.0 0.0 CHANGE IS COMING...GET READY!!! Boom, Another [CB] Jab, Nothing Can Stop This! Globalism at its end stage, [CB] push to make a one world govt. coming to an end. 
 null & Leaders Will Have to Follow the Majority!!! null null null null null null null null null null null null null null null null null null null null null null null null null 1.13297707692193382E18 ltonews LTONEWS null 2019-05-27T11:49:19.000Z 0.0 14.0 2.0 One of the useful articles of Stefan; here is the guide, you can run a @LTOnetwork node on Alibaba Cloud.
 null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 1.13087835537550118E18 giving_airdrops Daily_Airdrops null 2019-05-21T16:49:45.000Z 47.0 81.0 84.0 BTC IS STILL GOING STRONG!!
 null we are giving away 0.04 BTC and 10 BNB to 2 lucky winners! null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null 1.13120866242335539E18 Cybintelligence CybIntelligence null 2

Databricks data profile. Run in Databricks to view.

### Missing Values

In [0]:
%sql
SELECT
SUM(case when id IS NULL THEN 1 ELSE 0 END) AS id_null,
SUM(case when user IS NULL THEN 1 ELSE 0 END) AS user_null,
SUM(case when fullname IS NULL THEN 1 ELSE 0 END) AS fullname_null,
SUM(case when url IS NULL THEN 1 ELSE 0 END) AS url_null,
SUM(case when timestamp IS NULL THEN 1 ELSE 0 END) AS timestamp_null,
SUM(case when replies IS NULL THEN 1 ELSE 0 END) AS replies_null,
SUM(case when likes IS NULL THEN 1 ELSE 0 END) AS likes_null,
SUM(case when retweets IS NULL THEN 1 ELSE 0 END) AS retweets_null,
SUM(case when text IS NULL THEN 1 ELSE 0 END)
FROM (
    SELECT *
    FROM workspace.default.bitcoin_tweets AS t
    WHERE t.user IS NULL OR t.fullname IS NULL OR t.url IS NULL OR t.timestamp IS NULL OR t.replies IS NULL OR t.likes IS NULL OR t.retweets IS NULL OR t.text IS NULL
)


id_null user_null fullname_null url_null timestamp_null replies_null likes_null retweets_null SUM(CASEWHENtextISNULLTHEN1ELSE0END) 130179 118975 127272 225910 130380 130376 130381 130373 130346

In [0]:
def get_missing_val_percent(df):
    # calculate the missing and the percentage 
    cols = []
    for f in df.schema.fields:
        c = f.name
        #if f.dataType.simpleString() in ("float", "double"):
        #    expr = count(when(isnan(c), c)).alias(c)
        #else:
        expr = F.count(F.when(F.col(c).isNull(), c)).alias(c)
        cols.append(expr)

    mis = df.select(cols)

    mis_prc = mis.select([
        F.round(F.col(c) / row_count * 100, 2).alias(f"{c}_pct") 
        for c in mis.columns
    ])

    # one unique df 
    missing = mis.union(mis_prc)
    # create pd dataframe to have the visualization of missing
    pd_missing = missing.toPandas().transpose()
    pd_missing.columns = ['counts', 'percent']
    pd_missing['features'] = missing.columns
    return pd_missing

In [0]:
df_missing = get_missing_val_percent(df)
display(df_missing)

counts percent features 130179.0 56.51 id 118975.0 51.64 user 127272.0 55.24 fullname 225910.0 98.06 url 130380.0 56.59 timestamp 130376.0 56.59 replies 130381.0 56.59 likes 130373.0 56.59 retweets 130346.0 56.58 text

Databricks visualization. Run in Databricks to view.

In [0]:

condition = reduce(lambda a, b: a & b, [F.col(c).isNull() for c in df.columns])
df.filter(condition).count()

118945

118945 rows (51,6% of the total rows) are all null values so we delete those because don't give us any information and the imputation will be useless introducing noise in the dataset (especially for the feature *text*).

Since for my analysis the *text* feature is the most important and isn't possible to perform imputation, I make sure there aren't missing values for this feature

In [0]:
df_clean = df.filter(~condition)
df_clean = df.filter(df.text.isNotNull())

In [0]:
df_missing = get_missing_val_percent(df_clean)
display(df_missing)
df_clean.count()

counts percent features 36.0 0.02 id 0.0 0.0 user 3.0 0.0 fullname 96679.0 41.96 url 36.0 0.02 timestamp 36.0 0.02 replies 36.0 0.02 likes 28.0 0.01 retweets 0.0 0.0 text

100037

We can see a huge decrease in the percentage of the missing values in the cleaned dataset, that now has 100037 records


## Number Variables

In [0]:
num_var = df_clean[['likes','replies','retweets']]

In [0]:
high_val = reduce(lambda a, b: a & b, [F.col(c) > 100 for c in num_var.columns])
low_val = reduce(lambda a, b: a & b, [F.col(c) <= 100 for c in num_var.columns])

In [0]:
display(num_var.filter(high_val))

likes replies retweets 14470.0 790.0 5542.0 1335.0 164.0 161.0 1476.0 142.0 177.0 1870.0 213.0 1744.0 2653.0 352.0 727.0 4425.0 2104.0 5070.0 455.0 200.0 387.0 5549.0 115.0 1954.0 5910.0 244.0 1620.0 1863.0 143.0 201.0 607.0 500.0 540.0 458.0 338.0 346.0 1834.0 228.0 899.0 153.0 169.0 194.0 2246.0 209.0 2080.0 192.0 135.0 160.0 314.0 592.0 581.0 179.0 255.0 174.0 162.0 147.0 166.0 502.0 296.0 440.0 169.0 270.0 173.0 231.0 137.0 205.0 150.0 176.0 121.0 584.0 309.0 222.0 1396.0 131.0 284.0 1362.0 114.0 288.0 1075.0 132.0 203.0 4034.0 1209.0 1794.0 160.0 182.0 181.0 1755.0 312.0 314.0 126.0 132.0 120.0 116.0 131.0 116.0 1450.0 1076.0 1135.0 1266.0 157.0 357.0 187.0 156.0 145.0 267.0 389.0 347.0 2059.0 180.0 648.0 193.0 147.0 129.0 971.0 147.0 209.0 141.0 137.0 138.0 4163.0 185.0 1279.0 494.0 264.0 611.0 147.0 149.0 144.0 442.0 131.0 104.0 2807.0 136.0 468.0 118.0 122.0 112.0 303.0 284.0 312.0 214.0 258.0 173.0 238.0 346.0 108.0 1674.0 168.0 269.0 147.0 125.0 126.0 160.0 133.0 144.0 2565.0 125.0 362.0 117.0 114.0 122.0 995.0 971.0 956.0 509.0 188.0 227.0 2238.0 165.0 7816.0 3187.0 219.0 579.0 313.0 232.0 266.0 143.0 165.0 157.0 4106.0 112.0 1353.0 237.0 199.0 211.0 102.0 101.0 115.0 1660.0 193.0 201.0 5209.0 190.0 1790.0 416.0 138.0 376.0 181.0 178.0 149.0 11401.0 502.0 3370.0 160.0 160.0 190.0 1744.0 153.0 851.0 3870.0 343.0 808.0 2255.0 213.0 557.0 2273.0 313.0 561.0 2403.0 186.0 470.0 1008.0 195.0 210.0 3527.0 216.0 720.0 112.0 145.0 106.0 4810.0 258.0 1735.0 454.0 112.0 436.0 437.0 209.0 105.0 435.0 167.0 675.0 1507.0 109.0 330.0 615.0 328.0 222.0 2399.0 193.0 595.0 488.0 500.0 471.0 1217.0 226.0 244.0 519.0 199.0 132.0 1269.0 637.0 155.0 109.0 142.0 101.0 2378.0 187.0 618.0 1508.0 280.0 1366.0 2685.0 239.0 460.0 383.0 295.0 260.0 1229.0 197.0 530.0 3118.0 428.0 533.0 183.0 143.0 147.0 227.0 210.0 212.0 1318.0 168.0 765.0 1741.0 132.0 203.0 182.0 115.0 122.0 1394.0 173.0 187.0 1350.0 101.0 136.0 256.0 175.0 249.0 430.0 118.0 392.0 346.0 121.0 304.0 236.0 211.0 185.0 1679.0 120.0 577.0 1125.0 169.0 131.0 1098.0 1718.0 2268.0 1774.0 213.0 1250.0 472.0 454.0 378.0 762.0 116.0 135.0 1094.0 682.0 1574.0 605.0 340.0 117.0 3057.0 130.0 506.0 294.0 105.0 181.0

Databricks visualization. Run in Databricks to view.

In [0]:
display(num_var.filter(low_val))

likes replies retweets 0.0 0.0 0.0 0.0 0.0 0.0 2.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 14.0 0.0 2.0 81.0 47.0 84.0 2.0 3.0 7.0 1.0 1.0 1.0 0.0 0.0 0.0 0.0 0.0 1.0 1.0 1.0 1.0 19.0 1.0 6.0 40.0 14.0 39.0 28.0 1.0 4.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 1.0 1.0 12.0 3.0 8.0 0.0 0.0 0.0 94.0 8.0 76.0 0.0 1.0 1.0 0.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 1.0 42.0 3.0 8.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 28.0 4.0 16.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 46.0 4.0 30.0 0.0 0.0 0.0 14.0 2.0 8.0 0.0 0.0 1.0 12.0 1.0 6.0 0.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 5.0 0.0 2.0 69.0 0.0 51.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 29.0 1.0 7.0 29.0 4.0 7.0 0.0 0.0 0.0 76.0 1.0 49.0 0.0 0.0 0.0 0.0 0.0 0.0 3.0 0.0 2.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 63.0 0.0 47.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 3.0 0.0 2.0 11.0 0.0 6.0 0.0 0.0 0.0 0.0 0.0 0.0 51.0 2.0 11.0 82.0 1.0 54.0 7.0 0.0 3.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 92.0 0.0 61.0 6.0 0.0 1.0 27.0 2.0 7.0 7.0 2.0 3.0 2.0 1.0 1.0 86.0 0.0 53.0 47.0 0.0 56.0 45.0 55.0 45.0 36.0 0.0 35.0 72.0 0.0 50.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 2.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 64.0 0.0 41.0 0.0 0.0 1.0 66.0 0.0 41.0 36.0 1.0 12.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 54.0 8.0 6.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 89.0 17.0 8.0 21.0 38.0 37.0 70.0 43.0 64.0 0.0 0.0 1.0 13.0 0.0 13.0 0.0 0.0 1.0 4.0 1.0 2.0 62.0 0.0 36.0 19.0 0.0 16.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 3.0 0.0 2.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 4.0 1.0 3.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 1.0 9.0 0.0 2.0 6.0 0.0 4.0 9.0 0.0 2.0 6.0 0.0 3.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 2.0 5.0 0.0 1.0 6.0 0.0 3.0 59.0 1.0 45.0 31.0 3.0 20.0 0.0 0.0 1.0 68.0 2.0 38.0 17.0 11.0 2.0 28.0 7.0 3.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 63.0 0.0 57.0 0.0 0.0 0.0 61.0 3.0 8.0 4.0 0.0 1.0 31.0 0.0 29.0 74.0 0.0 54.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 50.0 0.0 44.0 4.0 0.0 2.0 1.0 0.0 2.0 12.0 1.0 17.0 67.0 36.0 74.0 0.0 0.0 0.0 31.0 15.0 23.0 57.0 1.0 53.0 54.0 0.0 45.0 51.0 0.0 38.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 3.0 0.0 3.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 46.0 0.0 41.0 55.0 1.0 45.0 29.0 2.0 5.0 0.0 0.0 1.0 0.0 0.0 0.0 2.0 12.0 2.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

The distribution of those variables is very right skewed. Even a boxplot visualization will be useless due to the outliers with high values. 

The median is in all 3 variables at 0.

Dividing the visualization by high and low values we can take a better look at the distribution of those variables.

The conclusion of this analysis is that the most of the tweets are beetween 0 and 10 values for *likes* and *retweet* and between 0 and 5 for *replies*.

## Text length analysis

In [0]:
from pyspark.sql.functions import length

df_clean = df_clean.withColumn("text_length", length("text"))
display(df_clean["text", "text_length"])

text text_length È appena uscito un nuovo video! LES CRYPTOMONNAIES QUI PULVÉRISENT BITCOIN EN 2019 https://t.co/yCsQMvRnyS 106 Cardano: Digitize Currencies; EOS https://t.co/1kTKqKEBlS 6500% ROI; AT&T Bitcoin Bill Pay https://t.co/eQCwOXKHK0 | Cardano (ADA) 🌏📢😎🤑💵 | #FolloForFolloBack #follo4folloback #followforfollow #bitcointe #cryptocurrency 225 Another Test tweet that wasn't caught in the stream ! bitcoin 61 Current Crypto Prices! 
 24 Spiv (Nosar Baz): BITCOIN Is An Asset & NOT A Currency.
 60 #btc inceldiği yerden kopsun bakalım 17:00 ye kadar bir hareket bekliyorum, yukarı yönlü olur umarın sanırım inşallah yani 😁 https://t.co/pIMyKfNtc8 148 @nwoodfine We have been building on the real #bitcoin SV.
 58 @pedronauck como investidor, vc é um ótimo dev. Sorte q eu comprei os BTC, subiu a poha toda :o 95 ブラジルはまぁ置いといてもドイツは存在感出してくるのかな。ロシアもマイニングなどで元気になるかと思ったらそこまででしたね。
 62 CHANGE IS COMING...GET READY!!! Boom, Another [CB] Jab, Nothing Can Stop This! Globalism at its end stage, [CB] push to make a one world govt. coming to an end. 
 162 One of the useful articles of Stefan; here is the guide, you can run a @LTOnetwork node on Alibaba Cloud.
 107 BTC IS STILL GOING STRONG!!
 28 BestMixer has been seized by the Dutch Police / Luxembourg Police and French Police w/ association from Europol. BestMixer was a Bitcoin Mixer/Tumbler. #Cryptocurrency #Bitcoin #BestMixer https://t.co/dXrEY9yAtt 211 Invested my Life Savings into Bitcoin and Ethereum | Vlog #09 https://t.co/CEL0BXw3fs https://t.co/AET16t8a56 109 Bitcoin Price Hits $8,939 in New 2019 High: What’s Driving the Hypnotic Rally? https://t.co/BADC8cBQdd 102 share 5 【毎日プレゼント企画】
 12 #Countdown #ComingSoon The $QLC airdrop, #Q_Gas tokens for every QLC holders, Don't waste the opportunity buy now and hold.
 124 You have roughly 6 days left to get your #LaunhPadFoundation 50/50 #raffle tickets in!! Current pot is around 16.5 #Litecoin!! Head over to https://t.co/qLTV0r5aF8 and grab your #tickets today!! #LTC #BTC #Crypto. #LitecoinFam #airdrop #DGB #DigiByte @jonnylitecoin @LTCFoundation https://t.co/aFIbK1Pd26 304 BTC IS GOING CRAZYYY!
 22 $HOT $HOT $HOT 🍀
 17 Running bitcoin 15 https://t.co/Ip0ph8uZYn
 24 Crypto prices rose across the board over the weekend as Bitcoin nears $9,000 level.
 84 https://t.co/6gs25lZoOO Outro grande banco holandês abandona lançamento de carteira para Criptomoedas. #bitnoticias #bitnada #bitcoin… https://t.co/qkfzMEWoHK 158 Bitcoin SV (BSV) Price Spikes 33%, Gains $1 Billion From a $55 Copyright Application - CCN https://t.co/DVF1AqJGxk https://t.co/7xIKJBb2e2 138 Global coin (GC) já começa errada, sendo uma coin pra brigar com BTC junta do governo e Centralizada, vocês não entenderam o Conceito do BTC ainda, né? https://t.co/dhEPv1Fm6P 175 Bitcoin Whales Move 27019 BTC in Crypto Rally – Plus Ripple and XRP, Ethereum, Litecoin, Stellar, Tron, Cardano - The Daily Hodl https://t.co/8W0dp4YKTi https://t.co/nElvOLiGdV 176 🤣🤣🤣 3 As Intel $INTC Valuation Rose, Btc Capital Management Has Increased by $418,968 Its Position; Schlumberger LTD $SLB Share Price Declined While Mcdaniel Terry & Co Cut by $1.42 Million Its Holding https://t.co/HmDE6GHvVW 223 This is true. Crypto currency is a new asset class people are just now beginning to understand. I'll see my fellow traders on the Moon. 135 @APompliano If by Bitcoin you mean BSV, I fully agree with you. However, if you're talking about BTC, you couldn't be more wrong. Five years from now nobody will even remember what BTC was 188 Pls save cuttoff 60/ 65 23 bitcoin may pump to 100k but I bet my ass 1DOGE=1BTC this season 64 @keyvandavani @TuurDemeester @100trillionUSD @jimmysong @ToneVays @TraceMayer How many sats per person? 
 105 Setelah bekerja sama dengan Microsoft untuk melacak biji kopinya menggunakan Blockchain, Starbucks kembali menjadi perbincangan. Bekerja sama dengan Bakkt, Starbucks di Amerika Serikat mungkin akan menerima BTC sebagai alat pembayaran tahun ini.
 246 @MarkMarkafv @SrCapilla @woonomic The V

Databricks visualization. Run in Databricks to view.

As expected the lenght (in characters) is very low, with the most of the tweets in range 0-100.

## Language detection

In [0]:

# (facoltativo) Preprocessing leggero
@F.udf("string")
def demojize_udf(text):
    if text is None:
        return ""
    return emoji.demojize(text, delimiters=(" ", " "))

df_lang = (
    df_clean.withColumn("text_emoji", demojize_udf(F.col("text")))
      .withColumn("clean_text", 
                  F.lower(F.regexp_replace(F.col("text_emoji"), r"http\S+|@\w+|#|\n|\r", "")))
)

# 1. DocumentAssembler
doc_assembler = DocumentAssembler() \
    .setInputCol("clean_text") \
    .setOutputCol("document")

# 2. Language detection
lang_detector = LanguageDetectorDL.pretrained("langdetect_dl", "xx") \
    .setInputCols(["document"]) \
    .setOutputCol("language")

# 3. Finisher
finisher = Finisher() \
    .setInputCols(["language"]) \
    .setOutputCols(["lang"]) \
    .setOutputAsArray(False)

# 4. Pipeline
lang_pipeline = Pipeline(stages=[doc_assembler, lang_detector, finisher])

# Fit & Transform
lang_model = lang_pipeline.fit(df_lang)
df_with_lang = lang_model.transform(df_lang)

# Mostra risultati
display(df_with_lang["text", "lang"])

---------------------------------------------------------------------------
AssertionError                            Traceback (most recent call last)
File <command-8219615832142784>, line 15
      8 df_lang = (
      9     df_clean.withColumn("text_emoji", demojize_udf(F.col("text")))
     10       .withColumn("clean_text", 
     11                   F.lower(F.regexp_replace(F.col("text_emoji"), r"http\S+|@\w+|#|\n|\r", "")))
     12 )
     14 # 1. DocumentAssembler
---> 15 doc_assembler = DocumentAssembler() \
     16     .setInputCol("clean_text") \
     17     .setOutputCol("document")
     19 # 2. Language detection
     20 lang_detector = LanguageDetectorDL.pretrained("langdetect_dl", "xx") \
     21     .setInputCols(["document"]) \
     22     .setOutputCol("language")

File /databricks/python/lib/python3.12/site-packages/pyspark/__init__.py:120, in keyword_only.<locals>.wrapper(self, *args, **kwargs)
    118     raise TypeError("Method %s forces keyword arguments." % func.__n

# Sentiment Analysis

The pre-process chosen for the analysis is TF-IDF representation. This because the model for the sentiment is already able to capture tone and context, besides TF-IDF is more stable and lighter (considering short text like tweets) then an embedding like Word2Vec.

Word2Vec could be take in consideration to involve the semantic in the sentiment analysis, but in second instance.

In [0]:
# UDF: conversione emoji → parole chiave
@F.udf(StringType())
def demojize_udf(text):
    if text is None:
        return ""
    return emoji.demojize(text, delimiters=(" ", " "))

In [0]:
df_clean = df_clean.withColumn("text_emoji", demojize_udf(F.col("text")))

In [0]:
clean_text = SQLTransformer(
    statement="""
        SELECT *,
            lower(regexp_replace(
                regexp_replace(
                    regexp_replace(
                        regexp_replace(text, 'http\\S+|www\\.\\S+', ''),
                        '@\\w+', ''),
                    '(^rt\\s+)|(#)', ''),
                '[\\t\\n\\r]+', ' ')
            ) AS clean_text
        FROM __THIS__
    """
)


In [0]:
# DocumentAssembler: trasforma la colonna text in Document type per Spark NLP
doc_assembler = DocumentAssembler() \
    .setInputCol("text") \
    .setOutputCol("document")

# SentenceDetector (opzionale, utile per testi multi-sentence)
sent_detector = SentenceDetector() \
    .setInputCols(["document"]) \
    .setOutputCol("sentences")

# Tokenizer Spark NLP
tokenizer = Tokenizer() \
    .setInputCols(["sentences"]) \
    .setOutputCol("token")

# Normalizer: rimuove punteggiatura, numeri o normalizza
normalizer = Normalizer() \
    .setInputCols(["token"]) \
    .setOutputCol("normalized") \
    .setLowercase(True) \
    .setCleanupPatterns(["[^\\p{L}\\p{M}\\p{Nd}_'\\-]+"])  # conserva lettere, apostrofi, trattini

# StopWordsCleaner: rimuove stopwords
stop_cleaner = StopWordsCleaner.pretrained() \
    .setInputCols(["normalized"]) \
    .setOutputCol("cleanTokens") \
    .setCaseSensitive(False)

# (Opzionale) Stemmer o Lemmatizer: aumenta generalizzazione
# stemmer = Stemmer().setInputCols(["cleanTokens"]).setOutputCol("stemmed")
# oppure usare LemmatizerModel se hai il modello
# lemmatizer = LemmatizerModel.pretrained().setInputCols(["cleanTokens"]).setOutputCol("lemmas")

# Finisher: trasforma annotazioni Spark NLP in colonne array<string>
finisher = Finisher() \
    .setInputCols(["cleanTokens"]) \
    .setOutputCols(["tokens"]) \
    .setOutputAsArray(True) \
    .setCleanAnnotations(False)


In [0]:
cv = CountVectorizer(inputCol="tokens", outputCol="rawFeatures",
                     vocabSize=20000, minDF=5.0)  # regola vocabSize e minDF
idf = IDF(inputCol="rawFeatures", outputCol="tfidfFeatures", minDocFreq=5)


In [0]:
from pyspark.ml.feature import NGram
ngram = NGram(n=2, inputCol="tokens", outputCol="bigrams")
# poi si può unire tokens+ngrams in unico input per CountVectorizer con UDF di concatenazione array


In [0]:
stages = [
    clean_text,
    doc_assembler,
    sent_detector,
    tokenizer,
    normalizer,
    stop_cleaner,
    finisher,
    cv,
    idf
]

pipeline = Pipeline(stages=stages)
pipeline_model = pipeline.fit(df)   # fai fit solo su un set rappresentativo (per costruire vocab)
df_transformed = pipeline_model.transform(df)
